In [1]:
import pandas as pd
import numpy as np

In [2]:
df_link_id = pd.read_csv('link_id(200113,v1,링크ID추가부여,김민기).csv', dtype={'ROUTE_ID': str})
df_visum_link = pd.read_csv('visum_link.csv')
df_visum_stop = pd.read_csv('visum_stop.csv')

df_columns = ['$LINEROUTEITEM:LINENAME', 'LINEROUTENAME', 'DIRECTIONCODE', 'INDEX', 'ISROUTEPOINT', 'NODENO', 'STOPPOINTNO', 'POSTLENGTH', 'ADDVAL']
df_line_route_items = pd.DataFrame(columns=df_columns)
df_line_route_items.to_csv('line_route_items.csv', index=False, encoding='utf-8-sig')

DIRECTIONCODE = '>'
POSTLENGTH = '0km'
ADDVAL = 0

i = 1
INDEX = 1
START_NODE = -1
NEXT_NODE = -1
prev_route_id = -1
prev_stop = -1
prev_link = -1
prev_link_no = -1

# df_link_id = df_link_id[(df_link_id['ROUTE_NAME'] == '1100') | (df_link_id['ROUTE_NAME'] == '1101')]
# df_link_id = df_link_id[(df_link_id['ROUTE_NAME'] == '1') | (df_link_id['ROUTE_NAME'] == '1100') | (df_link_id['ROUTE_NAME'] == '1101')]
for _, l in df_link_id.iterrows():
    print(i, '/', len(df_link_id), '(', i/len(df_link_id)*100, '%)')
    i = i + 1
    
    route_id = l['ROUTE_ID']
    route_name = l['ROUTE_NAME']
    link_id = l['LINK_ID']
    link_idx = l['INDEX']
    
    if prev_route_id != route_id:
        df_line_route_items.to_csv('line_route_items.csv', mode='a', index=False, encoding='utf-8-sig', header=False)
        df_line_route_items = pd.DataFrame(columns=df_columns)
        INDEX = 1
        START_NODE = -1
        NEXT_NODE = -1
        prev_stop = -1
        prev_link = -1
        prev_link_no = -1
    
    prev_route_id = route_id
    
    if prev_link == link_id:
        continue
    
    prev_link = link_id
    
    if INDEX == 1:
        if len(set(df_visum_link[(df_visum_link['LINK_ID'] == link_id)]['LINK_NO'])) > 1:
            df_vlink = df_visum_link[df_visum_link['LINK_ID'] == link_id]
        
            for _, vl in df_vlink.iterrows():
                link_no = vl['LINK_NO']
                
                if prev_link_no == link_no:
                    continue
                
                prev_link_no = link_no

                df_vstop = df_visum_stop[df_visum_stop['LINK_NO'] == link_no]
                df_vstop = df_vstop.sort_values(by=['INDEX', 'F_NODE'])

                for _, vs in df_vstop.iterrows():
                    if prev_stop == vs['STOP_NO']:
                        continue

                    prev_stop = vs['STOP_NO']
                    
                    if INDEX > 1:
                        df_line_route_items = df_line_route_items.append(pd.Series([route_id, route_name, DIRECTIONCODE, INDEX, 0, NEXT_NODE, '', POSTLENGTH, ADDVAL], index=df_columns), ignore_index=True)
                        INDEX = INDEX + 1

                    df_line_route_items = df_line_route_items.append(pd.Series([route_id, route_name, DIRECTIONCODE, INDEX, 1, '', vs['STOP_NO'], POSTLENGTH, ADDVAL], index=df_columns), ignore_index=True)
                    INDEX = INDEX + 1
                    START_NODE = vs['F_NODE']
                    NEXT_NODE = df_visum_link[(df_visum_link['LINK_ID'] == link_id) & (df_visum_link['F_NODE'] == START_NODE) & (df_visum_link['LINK_NO'] == link_no)].T_NODE.item()
        else:
            df_vlink = df_visum_link[df_visum_link['LINK_ID'] == link_id]
        
            for _, vl in df_vlink.iterrows():
                link_no = vl['LINK_NO']
                
                if prev_link_no == link_no:
                    continue
                
                prev_link_no = link_no

                df_vstop = df_visum_stop[df_visum_stop['LINK_NO'] == link_no]
                df_vstop = df_vstop.sort_values(by=['INDEX', 'F_NODE'])

                for _, vs in df_vstop.iterrows():
                    if prev_stop == vs['STOP_NO']:
                        continue

                    prev_stop = vs['STOP_NO']

                    df_line_route_items = df_line_route_items.append(pd.Series([route_id, route_name, DIRECTIONCODE, INDEX, 1, '', vs['STOP_NO'], POSTLENGTH, ADDVAL], index=df_columns), ignore_index=True)
                    INDEX = INDEX + 1
                    START_NODE = vs['F_NODE']
                    NEXT_NODE = df_visum_link[(df_visum_link['LINK_ID'] == link_id) & (df_visum_link['F_NODE'] == START_NODE) & (df_visum_link['LINK_NO'] == link_no)].T_NODE.item()
    else:
        df_vlink = df_visum_link[(df_visum_link['LINK_ID'] == link_id) & (df_visum_link['F_NODE'] == NEXT_NODE)]
        
        for _, vl in df_vlink.iterrows():
            link_no = vl['LINK_NO']
            
            if prev_link_no == link_no:
                continue
            
            prev_link_no = link_no
            
            df_line_route_items = df_line_route_items.append(pd.Series([route_id, route_name, DIRECTIONCODE, INDEX, 0, NEXT_NODE, '', POSTLENGTH, ADDVAL], index=df_columns), ignore_index=True)
            INDEX = INDEX + 1
            
            NEXT_NODE = vl['T_NODE']
            
            df_vstop = df_visum_stop[df_visum_stop['LINK_NO'] == link_no]
            df_vstop = df_vstop.sort_values(by=['INDEX', 'F_NODE'])

            for _, vs in df_vstop.iterrows():
                if prev_stop == vs['STOP_NO']:
                    continue
                
                prev_stop = vs['STOP_NO']
                
                df_line_route_items = df_line_route_items.append(pd.Series([route_id, route_name, DIRECTIONCODE, INDEX, 1, '', vs['STOP_NO'], POSTLENGTH, ADDVAL], index=df_columns), ignore_index=True)
                INDEX = INDEX + 1
                
        if len(set(df_visum_link[(df_visum_link['LINK_ID'] == link_id)]['LINK_NO'])) > 1:
            df_vlink = df_visum_link[(df_visum_link['LINK_ID'] == link_id) & (df_visum_link['F_NODE'] == NEXT_NODE)]
        
            for _, vl in df_vlink.iterrows():
                link_no = vl['LINK_NO']

                if prev_link_no == link_no:
                    continue

                prev_link_no = link_no

                df_line_route_items = df_line_route_items.append(pd.Series([route_id, route_name, DIRECTIONCODE, INDEX, 0, NEXT_NODE, '', POSTLENGTH, ADDVAL], index=df_columns), ignore_index=True)
                INDEX = INDEX + 1

                NEXT_NODE = vl['T_NODE']

                df_vstop = df_visum_stop[df_visum_stop['LINK_NO'] == link_no]
                df_vstop = df_vstop.sort_values(by=['INDEX', 'F_NODE'])

                for _, vs in df_vstop.iterrows():
                    if prev_stop == vs['STOP_NO']:
                        continue

                    prev_stop = vs['STOP_NO']

                    df_line_route_items = df_line_route_items.append(pd.Series([route_id, route_name, DIRECTIONCODE, INDEX, 1, '', vs['STOP_NO'], POSTLENGTH, ADDVAL], index=df_columns), ignore_index=True)
                    INDEX = INDEX + 1

df_line_route_items.to_csv('line_route_items.csv', mode='a', index=False, encoding='utf-8-sig', header=False)

1 / 55598 ( 0.001798625849850714 %)
2 / 55598 ( 0.003597251699701428 %)
3 / 55598 ( 0.005395877549552142 %)
4 / 55598 ( 0.007194503399402856 %)
5 / 55598 ( 0.00899312924925357 %)
6 / 55598 ( 0.010791755099104284 %)
7 / 55598 ( 0.012590380948954998 %)
8 / 55598 ( 0.014389006798805712 %)
9 / 55598 ( 0.016187632648656428 %)
10 / 55598 ( 0.01798625849850714 %)
11 / 55598 ( 0.019784884348357852 %)
12 / 55598 ( 0.021583510198208568 %)
13 / 55598 ( 0.023382136048059284 %)
14 / 55598 ( 0.025180761897909996 %)
15 / 55598 ( 0.02697938774776071 %)
16 / 55598 ( 0.028778013597611424 %)
17 / 55598 ( 0.03057663944746214 %)
18 / 55598 ( 0.032375265297312855 %)
19 / 55598 ( 0.034173891147163564 %)
20 / 55598 ( 0.03597251699701428 %)
21 / 55598 ( 0.037771142846864995 %)
22 / 55598 ( 0.039569768696715704 %)
23 / 55598 ( 0.04136839454656642 %)
24 / 55598 ( 0.043167020396417136 %)
25 / 55598 ( 0.04496564624626785 %)
26 / 55598 ( 0.04676427209611857 %)
27 / 55598 ( 0.04856289794596928 %)
28 / 55598 ( 0.0503

228 / 55598 ( 0.4100866937659628 %)
229 / 55598 ( 0.41188531961581354 %)
230 / 55598 ( 0.4136839454656642 %)
231 / 55598 ( 0.41548257131551497 %)
232 / 55598 ( 0.4172811971653656 %)
233 / 55598 ( 0.4190798230152164 %)
234 / 55598 ( 0.42087844886506715 %)
235 / 55598 ( 0.4226770747149178 %)
236 / 55598 ( 0.4244757005647686 %)
237 / 55598 ( 0.4262743264146192 %)
238 / 55598 ( 0.42807295226446995 %)
239 / 55598 ( 0.42987157811432064 %)
240 / 55598 ( 0.4316702039641714 %)
241 / 55598 ( 0.43346882981402207 %)
242 / 55598 ( 0.4352674556638728 %)
243 / 55598 ( 0.4370660815137235 %)
244 / 55598 ( 0.43886470736357425 %)
245 / 55598 ( 0.4406633332134249 %)
246 / 55598 ( 0.4424619590632757 %)
247 / 55598 ( 0.4442605849131264 %)
248 / 55598 ( 0.44605921076297705 %)
249 / 55598 ( 0.44785783661282785 %)
250 / 55598 ( 0.4496564624626785 %)
251 / 55598 ( 0.45145508831252923 %)
252 / 55598 ( 0.4532537141623799 %)
253 / 55598 ( 0.45505234001223066 %)
254 / 55598 ( 0.45685096586208135 %)
255 / 55598 ( 0.

465 / 55598 ( 0.8363610201805821 %)
466 / 55598 ( 0.8381596460304328 %)
467 / 55598 ( 0.8399582718802834 %)
468 / 55598 ( 0.8417568977301343 %)
469 / 55598 ( 0.843555523579985 %)
470 / 55598 ( 0.8453541494298356 %)
471 / 55598 ( 0.8471527752796862 %)
472 / 55598 ( 0.8489514011295372 %)
473 / 55598 ( 0.8507500269793877 %)
474 / 55598 ( 0.8525486528292384 %)
475 / 55598 ( 0.8543472786790891 %)
476 / 55598 ( 0.8561459045289399 %)
477 / 55598 ( 0.8579445303787906 %)
478 / 55598 ( 0.8597431562286413 %)
479 / 55598 ( 0.8615417820784921 %)
480 / 55598 ( 0.8633404079283428 %)
481 / 55598 ( 0.8651390337781935 %)
482 / 55598 ( 0.8669376596280441 %)
483 / 55598 ( 0.8687362854778949 %)
484 / 55598 ( 0.8705349113277456 %)
485 / 55598 ( 0.8723335371775963 %)
486 / 55598 ( 0.874132163027447 %)
487 / 55598 ( 0.8759307888772978 %)
488 / 55598 ( 0.8777294147271485 %)
489 / 55598 ( 0.8795280405769992 %)
490 / 55598 ( 0.8813266664268498 %)
491 / 55598 ( 0.8831252922767007 %)
492 / 55598 ( 0.88492391812655

702 / 55598 ( 1.2626353465952014 %)
703 / 55598 ( 1.264433972445052 %)
704 / 55598 ( 1.2662325982949025 %)
705 / 55598 ( 1.2680312241447536 %)
706 / 55598 ( 1.2698298499946041 %)
707 / 55598 ( 1.2716284758444547 %)
708 / 55598 ( 1.2734271016943055 %)
709 / 55598 ( 1.2752257275441563 %)
710 / 55598 ( 1.2770243533940069 %)
711 / 55598 ( 1.2788229792438577 %)
712 / 55598 ( 1.2806216050937085 %)
713 / 55598 ( 1.282420230943559 %)
714 / 55598 ( 1.2842188567934099 %)
715 / 55598 ( 1.2860174826432604 %)
716 / 55598 ( 1.2878161084931112 %)
717 / 55598 ( 1.289614734342962 %)
718 / 55598 ( 1.2914133601928126 %)
719 / 55598 ( 1.2932119860426634 %)
720 / 55598 ( 1.2950106118925142 %)
721 / 55598 ( 1.2968092377423648 %)
722 / 55598 ( 1.2986078635922156 %)
723 / 55598 ( 1.3004064894420664 %)
724 / 55598 ( 1.302205115291917 %)
725 / 55598 ( 1.3040037411417678 %)
726 / 55598 ( 1.3058023669916183 %)
727 / 55598 ( 1.3076009928414691 %)
728 / 55598 ( 1.30939961869132 %)
729 / 55598 ( 1.3111982445411705 %

933 / 55598 ( 1.6781179179107164 %)
934 / 55598 ( 1.6799165437605668 %)
935 / 55598 ( 1.6817151696104178 %)
936 / 55598 ( 1.6835137954602686 %)
937 / 55598 ( 1.685312421310119 %)
938 / 55598 ( 1.68711104715997 %)
939 / 55598 ( 1.6889096730098203 %)
940 / 55598 ( 1.690708298859671 %)
941 / 55598 ( 1.6925069247095221 %)
942 / 55598 ( 1.6943055505593725 %)
943 / 55598 ( 1.6961041764092233 %)
944 / 55598 ( 1.6979028022590743 %)
945 / 55598 ( 1.6997014281089247 %)
946 / 55598 ( 1.7015000539587755 %)
947 / 55598 ( 1.7032986798086265 %)
948 / 55598 ( 1.7050973056584768 %)
949 / 55598 ( 1.7068959315083276 %)
950 / 55598 ( 1.7086945573581782 %)
951 / 55598 ( 1.710493183208029 %)
952 / 55598 ( 1.7122918090578798 %)
953 / 55598 ( 1.7140904349077304 %)
954 / 55598 ( 1.7158890607575812 %)
955 / 55598 ( 1.717687686607432 %)
956 / 55598 ( 1.7194863124572826 %)
957 / 55598 ( 1.7212849383071334 %)
958 / 55598 ( 1.7230835641569842 %)
959 / 55598 ( 1.7248821900068347 %)
960 / 55598 ( 1.7266808158566855 %

...

54461 / 55598 ( 97.95496240871974 %)
54462 / 55598 ( 97.95676103456958 %)
54463 / 55598 ( 97.95855966041944 %)
54464 / 55598 ( 97.96035828626928 %)
54465 / 55598 ( 97.96215691211914 %)
54466 / 55598 ( 97.963955537969 %)
54467 / 55598 ( 97.96575416381884 %)
54468 / 55598 ( 97.96755278966869 %)
54469 / 55598 ( 97.96935141551855 %)
54470 / 55598 ( 97.97115004136839 %)
54471 / 55598 ( 97.97294866721825 %)
54472 / 55598 ( 97.9747472930681 %)
54473 / 55598 ( 97.97654591891795 %)
54474 / 55598 ( 97.9783445447678 %)
54475 / 55598 ( 97.98014317061765 %)
54476 / 55598 ( 97.9819417964675 %)
54477 / 55598 ( 97.98374042231734 %)
54478 / 55598 ( 97.9855390481672 %)
54479 / 55598 ( 97.98733767401706 %)
54480 / 55598 ( 97.9891362998669 %)
54481 / 55598 ( 97.99093492571676 %)
54482 / 55598 ( 97.9927335515666 %)
54483 / 55598 ( 97.99453217741645 %)
54484 / 55598 ( 97.9963308032663 %)
54485 / 55598 ( 97.99812942911615 %)
54486 / 55598 ( 97.999928054966 %)
54487 / 55598 ( 98.00172668081586 %)
54488 / 5559

54692 / 55598 ( 98.37044498003526 %)
54693 / 55598 ( 98.3722436058851 %)
54694 / 55598 ( 98.37404223173496 %)
54695 / 55598 ( 98.3758408575848 %)
54696 / 55598 ( 98.37763948343465 %)
54697 / 55598 ( 98.37943810928451 %)
54698 / 55598 ( 98.38123673513437 %)
54699 / 55598 ( 98.38303536098421 %)
54700 / 55598 ( 98.38483398683407 %)
54701 / 55598 ( 98.38663261268391 %)
54702 / 55598 ( 98.38843123853376 %)
54703 / 55598 ( 98.39022986438361 %)
54704 / 55598 ( 98.39202849023346 %)
54705 / 55598 ( 98.39382711608332 %)
54706 / 55598 ( 98.39562574193317 %)
54707 / 55598 ( 98.39742436778302 %)
54708 / 55598 ( 98.39922299363286 %)
54709 / 55598 ( 98.40102161948272 %)
54710 / 55598 ( 98.40282024533256 %)
54711 / 55598 ( 98.40461887118241 %)
54712 / 55598 ( 98.40641749703227 %)
54713 / 55598 ( 98.40821612288212 %)
54714 / 55598 ( 98.41001474873197 %)
54715 / 55598 ( 98.41181337458183 %)
54716 / 55598 ( 98.41361200043167 %)
54717 / 55598 ( 98.41541062628151 %)
54718 / 55598 ( 98.41720925213137 %)
547

54934 / 55598 ( 98.80571243569912 %)
54935 / 55598 ( 98.80751106154898 %)
54936 / 55598 ( 98.80930968739882 %)
54937 / 55598 ( 98.81110831324868 %)
54938 / 55598 ( 98.81290693909854 %)
54939 / 55598 ( 98.81470556494838 %)
54940 / 55598 ( 98.81650419079823 %)
54941 / 55598 ( 98.81830281664809 %)
54942 / 55598 ( 98.82010144249793 %)
54943 / 55598 ( 98.82190006834777 %)
54944 / 55598 ( 98.82369869419763 %)
54945 / 55598 ( 98.82549732004749 %)
54946 / 55598 ( 98.82729594589733 %)
54947 / 55598 ( 98.82909457174719 %)
54948 / 55598 ( 98.83089319759704 %)
54949 / 55598 ( 98.83269182344688 %)
54950 / 55598 ( 98.83449044929674 %)
54951 / 55598 ( 98.8362890751466 %)
54952 / 55598 ( 98.83808770099644 %)
54953 / 55598 ( 98.8398863268463 %)
54954 / 55598 ( 98.84168495269614 %)
54955 / 55598 ( 98.84348357854599 %)
54956 / 55598 ( 98.84528220439584 %)
54957 / 55598 ( 98.84708083024569 %)
54958 / 55598 ( 98.84887945609555 %)
54959 / 55598 ( 98.8506780819454 %)
54960 / 55598 ( 98.85247670779525 %)
5496

55167 / 55598 ( 99.22479225871434 %)
55168 / 55598 ( 99.22659088456419 %)
55169 / 55598 ( 99.22838951041403 %)
55170 / 55598 ( 99.23018813626389 %)
55171 / 55598 ( 99.23198676211375 %)
55172 / 55598 ( 99.2337853879636 %)
55173 / 55598 ( 99.23558401381345 %)
55174 / 55598 ( 99.2373826396633 %)
55175 / 55598 ( 99.23918126551314 %)
55176 / 55598 ( 99.240979891363 %)
55177 / 55598 ( 99.24277851721286 %)
55178 / 55598 ( 99.2445771430627 %)
55179 / 55598 ( 99.24637576891256 %)
55180 / 55598 ( 99.2481743947624 %)
55181 / 55598 ( 99.24997302061225 %)
55182 / 55598 ( 99.2517716464621 %)
55183 / 55598 ( 99.25357027231195 %)
55184 / 55598 ( 99.2553688981618 %)
55185 / 55598 ( 99.25716752401166 %)
55186 / 55598 ( 99.25896614986151 %)
55187 / 55598 ( 99.26076477571135 %)
55188 / 55598 ( 99.26256340156121 %)
55189 / 55598 ( 99.26436202741105 %)
55190 / 55598 ( 99.2661606532609 %)
55191 / 55598 ( 99.26795927911076 %)
55192 / 55598 ( 99.26975790496061 %)
55193 / 55598 ( 99.27155653081046 %)
55194 / 55

55424 / 55598 ( 99.68703910212598 %)
55425 / 55598 ( 99.68883772797584 %)
55426 / 55598 ( 99.69063635382568 %)
55427 / 55598 ( 99.69243497967553 %)
55428 / 55598 ( 99.69423360552538 %)
55429 / 55598 ( 99.69603223137523 %)
55430 / 55598 ( 99.69783085722509 %)
55431 / 55598 ( 99.69962948307493 %)
55432 / 55598 ( 99.70142810892479 %)
55433 / 55598 ( 99.70322673477463 %)
55434 / 55598 ( 99.70502536062448 %)
55435 / 55598 ( 99.70682398647433 %)
55436 / 55598 ( 99.70862261232418 %)
55437 / 55598 ( 99.71042123817404 %)
55438 / 55598 ( 99.7122198640239 %)
55439 / 55598 ( 99.71401848987374 %)
55440 / 55598 ( 99.71581711572358 %)
55441 / 55598 ( 99.71761574157344 %)
55442 / 55598 ( 99.71941436742328 %)
55443 / 55598 ( 99.72121299327313 %)
55444 / 55598 ( 99.72301161912299 %)
55445 / 55598 ( 99.72481024497284 %)
55446 / 55598 ( 99.72660887082269 %)
55447 / 55598 ( 99.72840749667255 %)
55448 / 55598 ( 99.73020612252239 %)
55449 / 55598 ( 99.73200474837223 %)
55450 / 55598 ( 99.73380337422209 %)
55

In [2]:
result = pd.read_csv('line_route_items.csv')
result

$LINEROUTEITEM:LINENAME LINEROUTENAME DIRECTIONCODE  INDEX  \
0                   28010004.0             1             >      1   
1                   28010004.0             1             >      2   
2                   28010004.0             1             >      3   
3                   28010004.0             1             >      4   
4                   28010004.0             1             >      5   
5                   28010004.0             1             >      6   
6                   28010004.0             1             >      7   
7                   28010004.0             1             >      8   
8                   28010004.0             1             >      9   
9                   28010004.0             1             >     10   
10                  28010004.0             1             >     11   
11                  28010004.0             1             >     12   
12                  28010004.0             1             >     13   
13                  28010004.0             1             >     14   
14                  28010004.0             1             >     15   
15                  28010004.0             1             >     16   
16                  28010004.0             1             >     17   
17                  28010004.0             1             >     18   
18                  28010004.0             1             >     19   
19                  28010004.0             1             >     20   
20                  28010004.0             1             >     21   
21                  28010004.0             1             >     22   
22                  28010004.0             1             >     23   
23                  28010004.0             1             >     24   
24                  28010004.0             1             >     25   
25                  28010004.0             1             >     26   
26                  28010004.0             1             >     27   
27                  28010004.0             1             >     28   
28                  28010004.0             1             >     29   
29                  28010004.0             1             >     30   
...                        ...           ...           ...    ...   
57701               28315044.0         중구6-1             >    220   
57702               28315044.0         중구6-1             >    221   
57703               28315044.0         중구6-1             >    222   
57704               28315044.0         중구6-1             >    223   
57705               28315044.0         중구6-1             >    224   
57706               28315044.0         중구6-1             >    225   
57707               28315044.0         중구6-1             >    226   
57708               28315044.0         중구6-1             >    227   
57709               28315044.0         중구6-1             >    228   
57710               28315044.0         중구6-1             >    229   
57711               28315044.0         중구6-1             >    230   
57712               28315044.0         중구6-1             >    231   
57713               28315044.0         중구6-1             >    232   
57714               28315044.0         중구6-1             >    233   
57715               28315044.0         중구6-1             >    234   
57716               28315044.0         중구6-1             >    235   
57717               28315044.0         중구6-1             >    236   
57718               28315044.0         중구6-1             >    237   
57719               28315044.0         중구6-1             >    238   
57720               28315044.0         중구6-1             >    239   
57721               28315044.0         중구6-1             >    240   
57722               28315044.0         중구6-1             >    241   
57723               28315044.0         중구6-1             >    242   
57724               28315044.0         중구6-1             >    243   
57725               28315044.0         중구6-1             >    244   
57726               28315044.0         중구6-1             >    245   
57727

In [5]:
df_link_id = pd.read_csv('link_id(200113,v1,링크ID추가부여,김민기).csv', dtype={'ROUTE_ID': str})
df_visum_link = pd.read_csv('visum_link.csv')
df_visum_stop = pd.read_csv('visum_stop.csv')

df_columns = ['$TIMEPROFILEITEM:LINENAME', 'LINEROUTENAME', 'DIRECTIONCODE', 'TIMEPROFILENAME', 'INDEX', 'LRITEMINDEX', 'ALIGHT', 'BOARD', 'ARR', 'DEP', 'NUMFAREPOINTS', 'NUMFAREPOINTSBOARD', 'NUMFAREPOINTSTHROUGH', 'NUMFAREPOINTSALIGHT', 'ADDVAL']
df_time_profile_items = pd.DataFrame(columns=df_columns)
df_time_profile_items.to_csv('time_profile_items.csv', index=False, encoding='utf-8-sig')

i = 1
INDEX = 1
START_NODE = -1
NEXT_NODE = -1
prev_route_id = -1
prev_stop = -1
prev_link = -1
prev_link_no = -1
ARR = '00:00:00'
DEP = '00:00:00'

# df_link_id = df_link_id[(df_link_id['ROUTE_NAME'] == '1100') | (df_link_id['ROUTE_NAME'] == '1101')]
# df_link_id = df_link_id[(df_link_id['ROUTE_NAME'] == '1') | (df_link_id['ROUTE_NAME'] == '1100') | (df_link_id['ROUTE_NAME'] == '1101')]
for _, l in df_link_id.iterrows():
    print(i, '/', len(df_link_id), '(', i/len(df_link_id)*100, '%)')
    i = i + 1
    
    route_id = l['ROUTE_ID']
    route_name = l['ROUTE_NAME']
    link_id = l['LINK_ID']
    link_idx = l['INDEX']
    
    if prev_route_id != route_id:
        df_time_profile_items.to_csv('time_profile_items.csv', mode='a', index=False, encoding='utf-8-sig', header=False)
        df_time_profile_items = pd.DataFrame(columns=df_columns)
        INDEX = 1
        START_NODE = -1
        NEXT_NODE = -1
        prev_stop = -1
        prev_link = -1
        prev_link_no = -1
    
    prev_route_id = route_id
    
    if prev_link == link_id:
        continue
    
    prev_link = link_id
    
    if INDEX == 1:
        if len(set(df_visum_link[(df_visum_link['LINK_ID'] == link_id)]['LINK_NO'])) > 1:
            df_vlink = df_visum_link[df_visum_link['LINK_ID'] == link_id]
        
            for _, vl in df_vlink.iterrows():
                link_no = vl['LINK_NO']
                
                if prev_link_no == link_no:
                    continue
                
                prev_link_no = link_no

                df_vstop = df_visum_stop[df_visum_stop['LINK_NO'] == link_no]
                df_vstop = df_vstop.sort_values(by=['INDEX', 'F_NODE'])

                for _, vs in df_vstop.iterrows():
                    if prev_stop == vs['STOP_NO']:
                        continue

                    prev_stop = vs['STOP_NO']
                    
#                     if INDEX > 1:
#                         pass
#                         df_line_route_items = df_line_route_items.append(pd.Series([route_id, route_name, DIRECTIONCODE, INDEX, 0, NEXT_NODE, '', POSTLENGTH, ADDVAL], index=df_columns), ignore_index=True)
#                         INDEX = INDEX + 1

                    df_time_profile_items = df_time_profile_items.append(pd.Series([route_id, route_name, '>', 1, INDEX, vs['STOP_NO'], 1, 1, ARR, DEP, 0, 0, 0, 0, 0], index=df_columns), ignore_index=True)
                    INDEX = INDEX + 1
                    START_NODE = vs['F_NODE']
                    NEXT_NODE = df_visum_link[(df_visum_link['LINK_ID'] == link_id) & (df_visum_link['F_NODE'] == START_NODE) & (df_visum_link['LINK_NO'] == link_no)].T_NODE.item()
        else:
            df_vlink = df_visum_link[df_visum_link['LINK_ID'] == link_id]
        
            for _, vl in df_vlink.iterrows():
                link_no = vl['LINK_NO']
                
                if prev_link_no == link_no:
                    continue
                
                prev_link_no = link_no

                df_vstop = df_visum_stop[df_visum_stop['LINK_NO'] == link_no]
                df_vstop = df_vstop.sort_values(by=['INDEX', 'F_NODE'])

                for _, vs in df_vstop.iterrows():
                    if prev_stop == vs['STOP_NO']:
                        continue

                    prev_stop = vs['STOP_NO']

                    df_time_profile_items = df_time_profile_items.append(pd.Series([route_id, route_name, '>', 1, INDEX, vs['STOP_NO'], 1, 1, ARR, DEP, 0, 0, 0, 0, 0], index=df_columns), ignore_index=True)
                    INDEX = INDEX + 1
                    START_NODE = vs['F_NODE']
                    NEXT_NODE = df_visum_link[(df_visum_link['LINK_ID'] == link_id) & (df_visum_link['F_NODE'] == START_NODE) & (df_visum_link['LINK_NO'] == link_no)].T_NODE.item()
    else:
        df_vlink = df_visum_link[(df_visum_link['LINK_ID'] == link_id) & (df_visum_link['F_NODE'] == NEXT_NODE)]
        
        for _, vl in df_vlink.iterrows():
            link_no = vl['LINK_NO']
            
            if prev_link_no == link_no:
                continue
            
            prev_link_no = link_no
            
#             df_time_profile_items = df_time_profile_items.append(pd.Series([route_id, route_name, DIRECTIONCODE, INDEX, 0, NEXT_NODE, '', POSTLENGTH, ADDVAL], index=df_columns), ignore_index=True)
#             INDEX = INDEX + 1
            
            NEXT_NODE = vl['T_NODE']
            
            df_vstop = df_visum_stop[df_visum_stop['LINK_NO'] == link_no]
            df_vstop = df_vstop.sort_values(by=['INDEX', 'F_NODE'])

            for _, vs in df_vstop.iterrows():
                if prev_stop == vs['STOP_NO']:
                    continue
                
                prev_stop = vs['STOP_NO']
                
                df_time_profile_items = df_time_profile_items.append(pd.Series([route_id, route_name, '>', 1, INDEX, vs['STOP_NO'], 1, 1, ARR, DEP, 0, 0, 0, 0, 0], index=df_columns), ignore_index=True)
                INDEX = INDEX + 1
                
        if len(set(df_visum_link[(df_visum_link['LINK_ID'] == link_id)]['LINK_NO'])) > 1:
            df_vlink = df_visum_link[(df_visum_link['LINK_ID'] == link_id) & (df_visum_link['F_NODE'] == NEXT_NODE)]
        
            for _, vl in df_vlink.iterrows():
                link_no = vl['LINK_NO']

                if prev_link_no == link_no:
                    continue

                prev_link_no = link_no

#                 df_time_profile_items = df_time_profile_items.append(pd.Series([route_id, route_name, DIRECTIONCODE, INDEX, 0, NEXT_NODE, '', POSTLENGTH, ADDVAL], index=df_columns), ignore_index=True)
#                 INDEX = INDEX + 1

                NEXT_NODE = vl['T_NODE']

                df_vstop = df_visum_stop[df_visum_stop['LINK_NO'] == link_no]
                df_vstop = df_vstop.sort_values(by=['INDEX', 'F_NODE'])

                for _, vs in df_vstop.iterrows():
                    if prev_stop == vs['STOP_NO']:
                        continue

                    prev_stop = vs['STOP_NO']

                    df_time_profile_items = df_time_profile_items.append(pd.Series([route_id, route_name, '>', 1, INDEX, vs['STOP_NO'], 1, 1, ARR, DEP, 0, 0, 0, 0, 0], index=df_columns), ignore_index=True)
                    INDEX = INDEX + 1

df_time_profile_items.to_csv('time_profile_items.csv', mode='a', index=False, encoding='utf-8-sig', header=False)

1 / 55598 ( 0.001798625849850714 %)
2 / 55598 ( 0.003597251699701428 %)
3 / 55598 ( 0.005395877549552142 %)
4 / 55598 ( 0.007194503399402856 %)
5 / 55598 ( 0.00899312924925357 %)
6 / 55598 ( 0.010791755099104284 %)
7 / 55598 ( 0.012590380948954998 %)
8 / 55598 ( 0.014389006798805712 %)
9 / 55598 ( 0.016187632648656428 %)
10 / 55598 ( 0.01798625849850714 %)
11 / 55598 ( 0.019784884348357852 %)
12 / 55598 ( 0.021583510198208568 %)
13 / 55598 ( 0.023382136048059284 %)
14 / 55598 ( 0.025180761897909996 %)
15 / 55598 ( 0.02697938774776071 %)
16 / 55598 ( 0.028778013597611424 %)
17 / 55598 ( 0.03057663944746214 %)
18 / 55598 ( 0.032375265297312855 %)
19 / 55598 ( 0.034173891147163564 %)
20 / 55598 ( 0.03597251699701428 %)
21 / 55598 ( 0.037771142846864995 %)
22 / 55598 ( 0.039569768696715704 %)
23 / 55598 ( 0.04136839454656642 %)
24 / 55598 ( 0.043167020396417136 %)
25 / 55598 ( 0.04496564624626785 %)
26 / 55598 ( 0.04676427209611857 %)
27 / 55598 ( 0.04856289794596928 %)
28 / 55598 ( 0.0503

256 / 55598 ( 0.4604482175617828 %)
257 / 55598 ( 0.4622468434116335 %)
258 / 55598 ( 0.46404546926148427 %)
259 / 55598 ( 0.46584409511133495 %)
260 / 55598 ( 0.4676427209611857 %)
261 / 55598 ( 0.46944134681103633 %)
262 / 55598 ( 0.47123997266088713 %)
263 / 55598 ( 0.47303859851073776 %)
264 / 55598 ( 0.4748372243605885 %)
265 / 55598 ( 0.4766358502104392 %)
266 / 55598 ( 0.47843447606028994 %)
267 / 55598 ( 0.4802331019101406 %)
268 / 55598 ( 0.48203172775999137 %)
269 / 55598 ( 0.48383035360984206 %)
270 / 55598 ( 0.4856289794596928 %)
271 / 55598 ( 0.48742760530954354 %)
272 / 55598 ( 0.48922623115939423 %)
273 / 55598 ( 0.491024857009245 %)
274 / 55598 ( 0.4928234828590956 %)
275 / 55598 ( 0.4946221087089464 %)
276 / 55598 ( 0.49642073455879704 %)
277 / 55598 ( 0.4982193604086478 %)
278 / 55598 ( 0.5000179862584985 %)
279 / 55598 ( 0.5018166121083493 %)
280 / 55598 ( 0.5036152379581998 %)
281 / 55598 ( 0.5054138638080506 %)
282 / 55598 ( 0.5072124896579014 %)
283 / 55598 ( 0.50

531 / 55598 ( 0.9550703262707292 %)
532 / 55598 ( 0.9568689521205799 %)
533 / 55598 ( 0.9586675779704306 %)
534 / 55598 ( 0.9604662038202813 %)
535 / 55598 ( 0.962264829670132 %)
536 / 55598 ( 0.9640634555199827 %)
537 / 55598 ( 0.9658620813698334 %)
538 / 55598 ( 0.9676607072196841 %)
539 / 55598 ( 0.9694593330695349 %)
540 / 55598 ( 0.9712579589193856 %)
541 / 55598 ( 0.9730565847692363 %)
542 / 55598 ( 0.9748552106190871 %)
543 / 55598 ( 0.9766538364689378 %)
544 / 55598 ( 0.9784524623187885 %)
545 / 55598 ( 0.980251088168639 %)
546 / 55598 ( 0.98204971401849 %)
547 / 55598 ( 0.9838483398683406 %)
548 / 55598 ( 0.9856469657181912 %)
549 / 55598 ( 0.9874455915680419 %)
550 / 55598 ( 0.9892442174178928 %)
551 / 55598 ( 0.9910428432677434 %)
552 / 55598 ( 0.9928414691175941 %)
553 / 55598 ( 0.994640094967445 %)
554 / 55598 ( 0.9964387208172956 %)
555 / 55598 ( 0.9982373466671463 %)
556 / 55598 ( 1.000035972516997 %)
557 / 55598 ( 1.0018345983668477 %)
558 / 55598 ( 1.0036332242166985 %

776 / 55598 ( 1.395733659484154 %)
777 / 55598 ( 1.3975322853340049 %)
778 / 55598 ( 1.3993309111838554 %)
779 / 55598 ( 1.4011295370337062 %)
780 / 55598 ( 1.402928162883557 %)
781 / 55598 ( 1.4047267887334076 %)
782 / 55598 ( 1.4065254145832584 %)
783 / 55598 ( 1.4083240404331092 %)
784 / 55598 ( 1.4101226662829598 %)
785 / 55598 ( 1.4119212921328106 %)
786 / 55598 ( 1.4137199179826614 %)
787 / 55598 ( 1.415518543832512 %)
788 / 55598 ( 1.4173171696823628 %)
789 / 55598 ( 1.4191157955322133 %)
790 / 55598 ( 1.4209144213820641 %)
791 / 55598 ( 1.422713047231915 %)
792 / 55598 ( 1.4245116730817655 %)
793 / 55598 ( 1.426310298931616 %)
794 / 55598 ( 1.4281089247814671 %)
795 / 55598 ( 1.4299075506313177 %)
796 / 55598 ( 1.4317061764811683 %)
797 / 55598 ( 1.4335048023310193 %)
798 / 55598 ( 1.4353034281808699 %)
799 / 55598 ( 1.4371020540307204 %)
800 / 55598 ( 1.4389006798805712 %)
801 / 55598 ( 1.440699305730422 %)
802 / 55598 ( 1.4424979315802726 %)
803 / 55598 ( 1.4442965574301234 %

1019 / 55598 ( 1.8327997409978776 %)
1020 / 55598 ( 1.8345983668477284 %)
1021 / 55598 ( 1.8363969926975792 %)
1022 / 55598 ( 1.8381956185474297 %)
1023 / 55598 ( 1.8399942443972805 %)
1024 / 55598 ( 1.8417928702471311 %)
1025 / 55598 ( 1.843591496096982 %)
1026 / 55598 ( 1.8453901219468327 %)
1027 / 55598 ( 1.8471887477966833 %)
1028 / 55598 ( 1.848987373646534 %)
1029 / 55598 ( 1.850785999496385 %)
1030 / 55598 ( 1.8525846253462355 %)
1031 / 55598 ( 1.8543832511960863 %)
1032 / 55598 ( 1.856181877045937 %)
1033 / 55598 ( 1.8579805028957876 %)
1034 / 55598 ( 1.8597791287456384 %)
1035 / 55598 ( 1.8615777545954888 %)
1036 / 55598 ( 1.8633763804453398 %)
1037 / 55598 ( 1.8651750062951906 %)
1038 / 55598 ( 1.866973632145041 %)
1039 / 55598 ( 1.868772257994892 %)
1040 / 55598 ( 1.8705708838447428 %)
1041 / 55598 ( 1.8723695096945931 %)
1042 / 55598 ( 1.8741681355444442 %)
1043 / 55598 ( 1.875966761394295 %)
1044 / 55598 ( 1.8777653872441453 %)
1045 / 55598 ( 1.8795640130939963 %)
1046 / 5

...

54501 / 55598 ( 98.02690744271376 %)
54502 / 55598 ( 98.02870606856362 %)
54503 / 55598 ( 98.03050469441347 %)
54504 / 55598 ( 98.03230332026331 %)
54505 / 55598 ( 98.03410194611317 %)
54506 / 55598 ( 98.03590057196303 %)
54507 / 55598 ( 98.03769919781287 %)
54508 / 55598 ( 98.03949782366273 %)
54509 / 55598 ( 98.04129644951257 %)
54510 / 55598 ( 98.04309507536242 %)
54511 / 55598 ( 98.04489370121227 %)
54512 / 55598 ( 98.04669232706212 %)
54513 / 55598 ( 98.04849095291198 %)
54514 / 55598 ( 98.05028957876183 %)
54515 / 55598 ( 98.05208820461168 %)
54516 / 55598 ( 98.05388683046152 %)
54517 / 55598 ( 98.05568545631138 %)
54518 / 55598 ( 98.05748408216122 %)
54519 / 55598 ( 98.05928270801107 %)
54520 / 55598 ( 98.06108133386093 %)
54521 / 55598 ( 98.06287995971078 %)
54522 / 55598 ( 98.06467858556063 %)
54523 / 55598 ( 98.06647721141049 %)
54524 / 55598 ( 98.06827583726033 %)
54525 / 55598 ( 98.07007446311017 %)
54526 / 55598 ( 98.07187308896003 %)
54527 / 55598 ( 98.07367171480989 %)
5

54737 / 55598 ( 98.45138314327853 %)
54738 / 55598 ( 98.45318176912838 %)
54739 / 55598 ( 98.45498039497824 %)
54740 / 55598 ( 98.4567790208281 %)
54741 / 55598 ( 98.45857764667794 %)
54742 / 55598 ( 98.4603762725278 %)
54743 / 55598 ( 98.46217489837764 %)
54744 / 55598 ( 98.46397352422748 %)
54745 / 55598 ( 98.46577215007734 %)
54746 / 55598 ( 98.4675707759272 %)
54747 / 55598 ( 98.46936940177704 %)
54748 / 55598 ( 98.4711680276269 %)
54749 / 55598 ( 98.47296665347675 %)
54750 / 55598 ( 98.47476527932659 %)
54751 / 55598 ( 98.47656390517643 %)
54752 / 55598 ( 98.47836253102629 %)
54753 / 55598 ( 98.48016115687615 %)
54754 / 55598 ( 98.481959782726 %)
54755 / 55598 ( 98.48375840857585 %)
54756 / 55598 ( 98.4855570344257 %)
54757 / 55598 ( 98.48735566027554 %)
54758 / 55598 ( 98.4891542861254 %)
54759 / 55598 ( 98.49095291197526 %)
54760 / 55598 ( 98.4927515378251 %)
54761 / 55598 ( 98.49455016367496 %)
54762 / 55598 ( 98.4963487895248 %)
54763 / 55598 ( 98.49814741537465 %)
54764 / 555

54984 / 55598 ( 98.89564372819166 %)
54985 / 55598 ( 98.89744235404152 %)
54986 / 55598 ( 98.89924097989137 %)
54987 / 55598 ( 98.90103960574122 %)
54988 / 55598 ( 98.90283823159106 %)
54989 / 55598 ( 98.90463685744092 %)
54990 / 55598 ( 98.90643548329076 %)
54991 / 55598 ( 98.90823410914061 %)
54992 / 55598 ( 98.91003273499047 %)
54993 / 55598 ( 98.91183136084032 %)
54994 / 55598 ( 98.91362998669017 %)
54995 / 55598 ( 98.91542861254003 %)
54996 / 55598 ( 98.91722723838987 %)
54997 / 55598 ( 98.91902586423971 %)
54998 / 55598 ( 98.92082449008957 %)
54999 / 55598 ( 98.92262311593942 %)
55000 / 55598 ( 98.92442174178927 %)
55001 / 55598 ( 98.92622036763913 %)
55002 / 55598 ( 98.92801899348898 %)
55003 / 55598 ( 98.92981761933882 %)
55004 / 55598 ( 98.93161624518868 %)
55005 / 55598 ( 98.93341487103852 %)
55006 / 55598 ( 98.93521349688838 %)
55007 / 55598 ( 98.93701212273824 %)
55008 / 55598 ( 98.93881074858808 %)
55009 / 55598 ( 98.94060937443793 %)
55010 / 55598 ( 98.94240800028778 %)
5

55274 / 55598 ( 99.41724522464837 %)
55275 / 55598 ( 99.41904385049823 %)
55276 / 55598 ( 99.42084247634807 %)
55277 / 55598 ( 99.42264110219791 %)
55278 / 55598 ( 99.42443972804777 %)
55279 / 55598 ( 99.42623835389762 %)
55280 / 55598 ( 99.42803697974747 %)
55281 / 55598 ( 99.42983560559733 %)
55282 / 55598 ( 99.43163423144718 %)
55283 / 55598 ( 99.43343285729702 %)
55284 / 55598 ( 99.43523148314688 %)
55285 / 55598 ( 99.43703010899672 %)
55286 / 55598 ( 99.43882873484657 %)
55287 / 55598 ( 99.44062736069642 %)
55288 / 55598 ( 99.44242598654628 %)
55289 / 55598 ( 99.44422461239613 %)
55290 / 55598 ( 99.44602323824598 %)
55291 / 55598 ( 99.44782186409583 %)
55292 / 55598 ( 99.44962048994567 %)
55293 / 55598 ( 99.45141911579553 %)
55294 / 55598 ( 99.45321774164539 %)
55295 / 55598 ( 99.45501636749523 %)
55296 / 55598 ( 99.45681499334509 %)
55297 / 55598 ( 99.45861361919494 %)
55298 / 55598 ( 99.46041224504478 %)
55299 / 55598 ( 99.46221087089464 %)
55300 / 55598 ( 99.46400949674448 %)
5

55503 / 55598 ( 99.82913054426417 %)
55504 / 55598 ( 99.83092917011403 %)
55505 / 55598 ( 99.83272779596388 %)
55506 / 55598 ( 99.83452642181373 %)
55507 / 55598 ( 99.83632504766359 %)
55508 / 55598 ( 99.83812367351344 %)
55509 / 55598 ( 99.83992229936328 %)
55510 / 55598 ( 99.84172092521314 %)
55511 / 55598 ( 99.84351955106298 %)
55512 / 55598 ( 99.84531817691284 %)
55513 / 55598 ( 99.8471168027627 %)
55514 / 55598 ( 99.84891542861254 %)
55515 / 55598 ( 99.85071405446239 %)
55516 / 55598 ( 99.85251268031224 %)
55517 / 55598 ( 99.85431130616209 %)
55518 / 55598 ( 99.85610993201193 %)
55519 / 55598 ( 99.85790855786179 %)
55520 / 55598 ( 99.85970718371165 %)
55521 / 55598 ( 99.86150580956149 %)
55522 / 55598 ( 99.86330443541135 %)
55523 / 55598 ( 99.8651030612612 %)
55524 / 55598 ( 99.86690168711104 %)
55525 / 55598 ( 99.8687003129609 %)
55526 / 55598 ( 99.87049893881075 %)
55527 / 55598 ( 99.8722975646606 %)
55528 / 55598 ( 99.87409619051046 %)
55529 / 55598 ( 99.8758948163603 %)
55530 